In [3]:
%load_ext autoreload
%autoreload 2

In [4]:
from Utils.DataLoader import DataLoader
from Utils.DataAnalysis import DataAnalysis
from Utils.DataTransformer import DataTransformer
import pandas as pd
import matplotlib.pyplot as plt
from typing import List, Tuple
from Utils import PandasNotebookConfigs

In [5]:
DATA_LOADER = DataLoader()
DATA_ANALYSIS = DataAnalysis()
DATA_TRANSFORMER = DataTransformer()

PandasNotebookConfigs.config()

Ajustando display.float.format para %.2f


In [6]:
# for user_logs_df in DATA_LOADER.load_user_logs_df_in_chunks(chunksize=100_000):
#     copy_user_logs_df = user_logs_df.copy()
#     break

copy_user_logs_df = DATA_LOADER.load_user_logs_df()

In [7]:
copy_user_logs_df.head()

msno   safra  num_25  num_50  \
0  SwlrSivYHoKF9V5wm1YYYAnjHpd9y3OPjI9rDUhGJ3k=  201701     121      28   
1  rE5wSmHEF1Dhu55zhkiGB1HvotdlSHcIMGXv6VcqO2A=  201605      26       2   
2  hx+cyaQ/Jcdr/Z5foa/Cn0PXUzC/F7QO/NQvWQS1Qtc=  201611     161      71   
3  53QW6B70J23X2UCvxaaUppjyE0b6X9nzP79W4huZv+Q=  201502      37       9   
4  /0S1N/oRyxGLZlzxnW5rOjfo0ZAls9EH23ahuDNuqz8=  201506     205      49   

   num_75  num_985  num_100  num_unq  total_secs  total_hours  
0      14       29      704      827      184606        51.28  
1       5        6      462      256      119439        33.18  
2      49       34      668      891      204791        56.89  
3       3        9      408      447      101186        28.11  
4      23       21      225      489       69957        19.43

In [8]:
copy_user_logs_df = copy_user_logs_df.sort_values(by=['msno', 'safra'])

In [9]:
copy_user_logs_df = DATA_TRANSFORMER.create_cost_column(copy_user_logs_df)

In [ ]:
copy_user_logs_df.to_csv('../data/preprocessed-user-logs-df.csv', index=False)

In [10]:
copy_user_logs_df.head()

msno   safra  num_25  \
4137945   +++4vcS9aMH7KWdfh5git6nA5fC5jjisd5H/NcM++WM=  201504       1   
11490586  +++EI4HgyhgcJHIPXk/VRP7bt17+2joG39T6oEfJ+tc=  201604       2   
12975182  +++FOrTS7ab3tIgIh8eWwX4FqRv8w/FoiOuyXsFvphY=  201609      60   
1173800   +++IZseRRiQS9aaSkH6cMYU6bGDcxUieAi/tH67sC5s=  201501      16   
17686478  +++IZseRRiQS9aaSkH6cMYU6bGDcxUieAi/tH67sC5s=  201502      23   

          num_50  num_75  num_985  num_100  num_unq  total_secs  total_hours  \
4137945        1       0        0        0        2          97         0.03   
11490586       0       0        0        0        1          56         0.02   
12975182      12      14        7      171      179       49996        13.89   
1173800        8      14        8     1831     1472      446494       124.03   
17686478      11       1        5      775      551      186845        51.90   

           cost  
4137945   50.02  
11490586  50.01  
12975182  55.91  
1173800  102.16  
17686478  71.49

In [ ]:
result_df = []
count = 0
for transactions_chunk in DATA_LOADER.load_transactions_df_in_chunks(chunksize=10_000):
    count += 10_000
    print(count)
    result_df.append(
        pd.merge(
            copy_user_logs_df,
            transactions_chunk,
            on=['msno', 'safra'],
            suffixes=('_user_logs', '_transactions'),
        )
    )
    

copy_user_logs_df = pd.concat(result_df, ignore_index=True)

10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
240000
250000
260000
270000
280000
290000
300000
310000
320000
330000
340000
350000
360000
370000
380000
390000
400000
410000
420000
430000
440000
450000
460000
470000
480000
490000
500000
510000
520000
530000
540000
550000
560000
570000
580000
590000
600000
610000
620000
630000
640000
650000
660000
670000
680000
690000
700000
710000
720000
730000
740000
750000
760000
770000
780000
790000
800000
810000
820000
830000
840000
850000
860000
870000
880000
890000
900000
910000
920000
930000
940000
950000
960000
970000
980000
990000
1000000
1010000
1020000
1030000
1040000
1050000
1060000
1070000
1080000
1090000
1100000
1110000
1120000
1130000


In [ ]:
copy_user_logs_df.to_csv('../data/preprocessed-merged.csv', index=False)

In [ ]:
# Testing with dask
import dask.dataframe as dd
import pandas as pd
from datetime import datetime
from dask.distributed import Client
from Utils.DataLoader import DataLoader
DATA_LOADER = DataLoader()

client = Client()

# Load the user logs DataFrame as a dask DataFrame
print(f'{datetime.now()} Init dask load data')
# dask_user_logs_df = dd.from_pandas(copy_user_logs_df, npartitions=10)
dask_user_logs_df = dd.read_csv('../data/preprocessed-user-logs-df.csv')
dask_user_logs_df['safra'] = dask_user_logs_df['safra'].astype('int32')

# Load the transactions DataFrame in chunks and merge with user logs
result_dask_df = []
count = 0
for transactions_chunk in DATA_LOADER.load_transactions_df_in_chunks(chunksize=10_000):
    count += 10_000
    dask_transactions_chunk = dd.from_pandas(transactions_chunk, npartitions=10)
    merged_chunk = dd.merge(
        dask_user_logs_df,
        dask_transactions_chunk,
        on=['msno', 'safra'],
        suffixes=('_user_logs', '_transactions')
    )
    result_dask_df.append(merged_chunk)
    print(count)


# Concatenate the dask DataFrames
print(f'{datetime.now()} Concating')
final_dask_df = dd.concat(result_dask_df)

# Compute the final DataFrame
print(f'{datetime.now()} Computing')
copy_user_logs_df = final_dask_df.compute()
print(copy_user_logs_df)


2025-02-22 14:32:15,290 - distributed.protocol.core - CRITICAL - Failed to deserialize
Traceback (most recent call last):
  File "/home/caio/Git-Projetos/2025-case-data-master-caio-arrabal/env/lib/python3.12/site-packages/distributed/protocol/core.py", line 175, in loads
    return msgpack.loads(
           ^^^^^^^^^^^^^^
  File "/home/caio/Git-Projetos/2025-case-data-master-caio-arrabal/env/lib/python3.12/site-packages/msgpack/fallback.py", line 136, in unpackb
    raise ExtraData(ret, unpacker._get_extradata())
msgpack.exceptions.ExtraData: unpack(b) received extra data.
2025-02-22 14:32:15,292 - distributed.core - ERROR - Exception while handling op register-client
Traceback (most recent call last):
  File "/home/caio/Git-Projetos/2025-case-data-master-caio-arrabal/env/lib/python3.12/site-packages/distributed/core.py", line 834, in _handle_comm
    result = await result
             ^^^^^^^^^^^^
  File "/home/caio/Git-Projetos/2025-case-data-master-caio-arrabal/env/lib/python3.12/si

2025-02-22 14:32:15.121058 Init dask load data


FutureCancelledError: ('repartitiontofewer-9b36dd2086d2b815dad31c7f7b4cb048', 0) cancelled for reason: scheduler-connection-lost.
Client lost the connection to the scheduler. Please check your connection and re-run your work.

In [ ]:
result_dask_df

In [ ]:
import polars as pl
from datetime import datetime
from Utils.DataLoader import DataLoader
DATA_LOADER = DataLoader()

# Load the user logs DataFrame as a polars DataFrame
print(f'{datetime.now()} Init polars load data')
# polars_user_logs_df = pl.read_csv('../data/preprocessed-user-logs-df.csv')
polars_user_logs_df = pl.read_parquet('../data/user_logs.parquet', low_memory=True)
# polars_user_logs_df = polars_user_logs_df.with_column(pl.col('safra').cast(pl.Int32))

# Load the transactions DataFrame in chunks and merge with user logs
result_polars_df = []
count = 0
for transactions_chunk in DATA_LOADER.load_transactions_df_in_chunks(chunksize=10_000):
    count += 10_000
    polars_transactions_chunk = pl.from_pandas(transactions_chunk)
    merged_chunk = polars_user_logs_df.join(
        polars_transactions_chunk,
        on=['msno', 'safra'],
        how='inner'
    )
    result_polars_df.append(merged_chunk)

# Concatenate the polars DataFrames
print(f'{datetime.now()} Concating')
final_polars_df = pl.concat(result_polars_df)

print(f'{datetime.now()} Computing')
print(final_polars_df)

In [ ]:
result_df = []
for members_df in DATA_LOADER.load_members_df_in_chunks(chunksize=10_000):
    result_df.append(
        pd.merge(
            copy_user_logs_df,
            members_df,
            on=['msno', 'safra'],
            suffixes=('_user_logs', '_transactions')
        )
    )

copy_user_logs_df = pd.concat(result_df, ignore_index=True)


In [ ]:
copy_user_logs_df.to_csv('../data/preprocessed.csv', index=False)

In [ ]:
copy_user_logs_df.head().T

In [ ]:
# Let's build a Machine Learning model
from sklearn.ensemble import RandomForestRegressor

model = RandomForestRegressor(
    n_jobs=-1,
    random_state=42, # Same as np.random.seed(42)
)

try:
    model.fit(
        copy_user_logs_df.drop(['cost', 'msno'], axis=1), # X
        copy_user_logs_df['cost'],              # Y
    )
except Exception as e:
    print(f'We need to convert string data to Float first!\n{e}')

In [ ]:
copy_user_logs_df.safra.value_counts()

In [ ]:
copy_user_logs_df

In [ ]:
copy_user_logs_df.groupby('msno').value_counts()

In [ ]:
copy_user_logs_df.groupby(['msno', 'safra']).filter(lambda x:print(x))